### TODO avant le tp

1. Sélectionner le kernel python 3.8 dans bin/pyhton3
2. Décommentez les deux lignes de codes pour installer les deux librairies python
3. Executez la cellule
4. Recommentez les deux lignes de code

In [31]:
#! pip install tqdm
#! pip install trimesh

Fin import fonctions_tp2_curvature


### Début du tp

In [32]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [33]:
import numpy as np
import trimesh
import os
import pickle 

from fonctions_tp2_courbure import *
from utils_tp2_curvature import *

In [34]:
############################################
### A MODIFIER avec votre chemin absolue ###
###     qui doit se dterminer par '/'    ###
############################################

#absolute_path = "/path/to/folder/"
absolute_path = "/home/nephozz/Documents/SN/M1/S8 - M/Modelisation Geo/TP2/"

############################################

path_sorties = absolute_path + "sorties/"
path_models3D = absolute_path + "models3D/"

## A modifier
nom_mesh = "camel" 

### Chargement de données

In [35]:
## Chargement du modèle 3D et de ses attributs
model, dictionnaire = load_mesh(path_models3D+nom_mesh+".obj")
## Visualisation
model.show()

## Voisinages k-nn

In [36]:
# Si profondeur == 1, alors les voisins directs correpondent au 1 plus proches voisins
profondeur_k = 3
voisins_directs = get_direct_neighbors(dictionnaire['nsommets'], dictionnaire['aretes'])
dict_knn = compute_knn(profondeur_k, dictionnaire['nsommets'], voisins_directs)

### Vérifications

In [37]:
##############################################################################
## Test n°1 : respect des dimensions
if (len(voisins_directs) != dictionnaire['nsommets'])  : print('Test n°1 : PAS OK --> problème de dimension dans voisins_directs')
else : print('Test n°1 : OK')
if (len(dict_knn) != dictionnaire['nsommets'])  : print('Test n°2 : PAS OK --> problème de dimension dans dict_knn')
else : print('Test n°2 : OK')

##############################################################################
## Test n°3 : voisins direct
with open(absolute_path+"/verite_terrain/"+nom_mesh+"_voisins_directs.pkl", 'rb') as f:
    loaded_dict_voisins_direct = pickle.load(f)
## verification 
if voisins_directs == loaded_dict_voisins_direct : print("Test n°3 : voisins_directs OK ")
else :  print("Test n°3 : voisins_directs PAS OK")

##############################################################################
## Test n°4
for k in range(5):
    ## creation du cit pour k-nn
    dict_knn = compute_knn(k, dictionnaire['nsommets'], voisins_directs)
    with open(absolute_path+"/verite_terrain/"+nom_mesh+"_"+str(k+1)+"_nn.pkl", 'rb') as f:
        loaded_dict = pickle.load(f)
    ## verification 
    if dict_knn == loaded_dict : print("Test n°"+str(k+4)+" : dict_knn OK")
    else :  print("Test n°"+str(k+2)+" : dict_knn PAS OK")
##############################################################################

Test n°1 : OK
Test n°2 : OK
Test n°3 : voisins_directs OK 
Test n°4 : dict_knn OK
Test n°5 : dict_knn OK
Test n°6 : dict_knn OK
Test n°7 : dict_knn OK
Test n°8 : dict_knn OK


## Courbure [Meynet 2019]

To estimate the mean curvature at a point p, we proceed by local least squares fitting of a quadric surface. 
* First we estimate an approximate tangent plane using Principal Component Analysis, which gives us an orthonormal frame $(u_x , u_y , u_z )$ such that u z is aligned with an approximate normal to the surface. We take $p$ as the origin of the coordinate system. 
  
* In this local frame, the neighbour $p_i$ of $p$ has coordinates $(x_i , y_i , z_i )$. We thus look for the quadric surface $Q(x, y) = ax^2 + by^2 + cxy + dx + ey + f$ minimizing:

$$\sum_{i} ||z_i − Q(x_i , y_i )||^2$$


* The mean curvature can then be directly estimated from the derivatives of $Q$ that are expressed easily by its coefficients:
  
$$Curv(p) = \frac{(1 + d^2 )a + (1 + e^2 )b − 4abc}{(1 + e^2 + d^2)^{3/2}}$$ 

In [41]:
## Profondeur du voisinage 
profondeur_k = 3

## Voisins directs et k-nn
voisins_directs = get_direct_neighbors(dictionnaire['nsommets'], dictionnaire['aretes'])
dict_knn = compute_knn(profondeur_k, dictionnaire['nsommets'], voisins_directs)

## Courbure moyenne et erreur résiduelle
curv_and_error = compute_mean_curvature(dictionnaire['sommets'], dict_knn)

100%|██████████| 20000/20000 [00:08<00:00, 2227.54it/s]


In [42]:
## Valeurs de courbure et d'erreur résiduelle en chaque sommet
curvature = curv_and_error[:,0]
residus = curv_and_error[:,1]

## Colormap en fonctiond es valeurs
colormap_curv = generate_colormap(curvature, 'jet')
colormap_residus = generate_colormap(residus, 'jet')

## Sauvagarde 
save(path_sorties+nom_mesh+"_curv_"+str(profondeur_k)+"nn.obj", path_models3D+nom_mesh+".obj", dictionnaire['sommets'], colormap_curv)
save(path_sorties+nom_mesh+"_residus_"+str(profondeur_k)+"nn.obj", path_models3D+nom_mesh+".obj", dictionnaire['sommets'], colormap_residus)

## Affichage coubure moyenne
load_mesh(path_sorties+nom_mesh+"_curv_"+str(profondeur_k)+"nn.obj")[0].show()

In [40]:
## Affichage residus
load_mesh(path_sorties+nom_mesh+"_residus_"+str(profondeur_k)+"nn.obj")[0].show()